In [29]:
from ultralytics import YOLO
from PIL import Image
from roboflow import Roboflow
import json
import numpy as np
import cv2
import matplotlib.pyplot as plt
import math

In [4]:
apikey = None
with open('apikey.json', 'r') as f:
    apikey = json.load(f)

In [33]:
rf = Roboflow(api_key=apikey['apikey'])
project = rf.workspace("bielglasses").project("barcelona-streets")
dataset = project.version(11).download("yolov8")

loading Roboflow workspace...
loading Roboflow project...
Dependency ultralytics==8.0.196 is required but found version=8.0.208, to fix: `pip install ultralytics==8.0.196`



Extracting Dataset Version Zip to Barcelona-Streets-11 in yolov8:: 100%|██████████| 9072/9072 [00:09<00:00, 957.09it/s] 


In [39]:
!yolo task=segment mode=train model=C:/Users/damem/Desktop/Object-detection-with-YOLO/runs/segment/train2/weights/best.pt data={dataset.location}/data.yaml epochs=50 imgsz=640

Ultralytics YOLOv8.0.208  Python-3.10.10 torch-2.0.0+cu118 CUDA:0 (NVIDIA GeForce RTX 4050 Laptop GPU, 6140MiB)
engine\trainer: task=segment, mode=train, model=C:/Users/damem/Desktop/Object-detection-with-YOLO/runs/segment/train2/weights/best.pt, data=c:\Users\damem\Desktop\Object-detection-with-YOLO\Barcelona-Streets-11/data.yaml, epochs=50, patience=50, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train3, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, show=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True, vid_stride=1, stream_buffer=Fals

In [ ]:
!yolo task=segment mode=val model=C:/Users/damem/Desktop/Object-detection-with-YOLO/runs/segment/train3/weights/best.pt data={dataset.location}/data.yaml

In [ ]:
!yolo task=detect mode=predict model=C:/Users/damem/Desktop/Object-detection-with-YOLO/runs/detect/train4/weights/best.pt source=C:/Users/damem/Desktop/Object-detection-with-YOLO/game-video.mp4

In [21]:
model = YOLO('runs/detect/train4/weights/best.pt')
results = model('Titans_Texans.jpg', conf=.1)
for result in results:
    pixels = result.plot()
    im = Image.fromarray(pixels[..., ::-1])
    im.show()


image 1/1 c:\Users\damem\Desktop\Object-detection-with-YOLO\Titans_Texans.jpg: 480x640 3 1s, 10 2s, 5 4s, 31.1ms
Speed: 4.0ms preprocess, 31.1ms inference, 4.0ms postprocess per image at shape (1, 3, 480, 640)


In [33]:
model = YOLO('runs/segment/train3/weights/best.pt')
result = model("Screenshot_1.png")

for r in result:
    mask = r.masks.xy[0]
    print(r.orig_shape)
    black_image = np.zeros(r.orig_shape)
    black_image = Image.fromarray(black_image)
    pixels = r.plot(boxes=False)
    for point in mask:
        print(point)
        black_image.putpixel((math.floor(point[0])-1, math.floor(point[1])-1), 255)
        
    black_image.show()


image 1/1 c:\Users\damem\Desktop\Object-detection-with-YOLO\Screenshot_1.png: 448x640 3 Curbs, 3 Grounds, 28.4ms
Speed: 3.0ms preprocess, 28.4ms inference, 4.0ms postprocess per image at shape (1, 3, 448, 640)


(597, 892)
[     282.93      170.28]
[     281.54      171.67]
[     260.63      171.67]
[     259.24      173.06]
[     262.02      175.85]
[     262.02      177.24]
[     266.21      181.43]
[      267.6      181.43]
[     268.99      182.82]
[     270.39      182.82]
[     273.18      185.61]
[     274.57      185.61]
[     275.96         187]
[     280.14         187]
[     281.54      188.39]
[     282.93      188.39]
[     285.72      191.18]
[     291.29      191.18]
[     299.66      199.54]
[     301.05      199.54]
[     308.02      206.51]
[     308.02      207.91]
[      312.2      212.09]
[      312.2      213.48]
[     313.59      214.88]
[     313.59      216.27]
[     314.99      217.66]
[     314.99      220.45]
[     316.38      221.84]
[     316.38      232.99]
[     313.59      235.78]
[     313.59      237.18]
[     308.02      242.75]
[     308.02      244.14]
[     306.62      245.54]
[     306.62      246.93]
[     298.26      255.29]
[     296.87      255.29]
[

In [42]:
model.export(format='onnx')

Ultralytics YOLOv8.0.208  Python-3.10.10 torch-2.0.0+cu118 CPU (12th Gen Intel Core(TM) i5-12450H)

PyTorch: starting from 'runs\segment\train3\weights\best.pt' with input shape (1, 3, 640, 640) BCHW and output shape(s) ((1, 43, 8400), (1, 32, 160, 160)) (6.5 MB)
requirements: Ultralytics requirement ['onnx>=1.12.0'] not found, attempting AutoUpdate...
     ---------------------------------------- 14.3/14.3 MB 9.3 MB/s eta 0:00:00

requirements: AutoUpdate success  21.0s, installed 1 package: ['onnx>=1.12.0']
requirements:  Restart runtime or rerun command for updates to take effect


ONNX: starting export with onnx 1.15.0 opset 17...
ONNX: export success  22.8s, saved as 'runs\segment\train3\weights\best.onnx' (12.6 MB)

Export complete (25.6s)
Results saved to C:\Users\damem\Desktop\Object-detection-with-YOLO\runs\segment\train3\weights
Predict:         yolo predict task=segment model=runs\segment\train3\weights\best.onnx imgsz=640  
Validate:        yolo val task=segment model=runs\

============= Diagnostic Run torch.onnx.export version 2.0.0+cu118 =============
verbose: False, log level: Level.ERROR
======================= 0 NONE 0 NOTE 0 WARNING 0 ERROR ========================



'runs\\segment\\train3\\weights\\best.onnx'